In [1]:
import MetaTrader5 as mt5
from datetime import datetime, timedelta, time

from __init__ import Backtester, get_ohlc_history, create_ohlc_fig, evaluate_backtest

In [2]:
if not mt5.initialize(): 
    print( 'initialization failed')
    quit() 
else: print('initialization success') 

login = 192918303
password = "Demo@1234"
server = "Exness-MT5Trial"

if not mt5.login(login, password, server):
    print("Failed to connect to the server")
else:
    print("Connected to the server successfully")
    print(mt5.account_info())


initialization success
Connected to the server successfully
AccountInfo(login=192918303, trade_mode=0, leverage=200, limit_orders=1024, margin_so_mode=0, trade_allowed=True, trade_expert=True, margin_mode=2, currency_digits=2, fifo_close=False, balance=10745.11, credit=0.0, profit=-2290.37, equity=8454.74, margin=1136.4, margin_free=7318.34, margin_level=743.993312214009, margin_so_call=60.0, margin_so_so=0.0, margin_initial=0.0, margin_maintenance=0.0, assets=0.0, liabilities=0.0, commission_blocked=0.0, name='DemoBotTester', server='Exness-MT5Trial', currency='USD', company='Exness Technologies Ltd')


In [7]:
import sys
sys.path.append('c:/Users/derne/OneDrive - The Pennsylvania State University/Programming/Extra/algobot/ATJ')

from config import initialize_mt5
initialize_mt5()

None


In [ ]:
symbol = 'BTCUSDm'
start_dt = datetime(2023, 1, 1)
end_dt = datetime.now()

# get historical data
# mt5.initialize()
ohlc = get_ohlc_history(symbol, mt5.TIMEFRAME_H1, start_dt, end_dt)

# prepare data set
ohlc['day'] = ohlc['time'].dt.dayofweek  
ohlc['time_hms'] = ohlc['time'].dt.time
ohlc['hour'] = ohlc['time'].dt.hour

ohlc['high_20'] = ohlc['high'].rolling(24*5).max().shift(1)
ohlc['low_20'] = ohlc['low'].rolling(24*5).min().shift(1)

ohlc['range'] = ohlc['high'] - ohlc['low']

ohlc = ohlc.dropna()
print(ohlc)

def get_entry_signal(x):
    if x['close'] > x['high_20']:
        return 'buy'
    
    elif x['close'] < x['low_20']:
        return 'sell'
    
def get_exit_signal(x):
    if x['close'] > x['high_20']:
        return 'buy'
    
    elif x['close'] < x['low_20']:
        return 'sell'

ohlc['signal'] = ohlc.apply(get_entry_signal, axis=1)
ohlc['exit_signal'] = ohlc.apply(get_exit_signal, axis=1)

ohlc_fig = create_ohlc_fig(ohlc)
ohlc_fig

                     time       open       high        low      close  day  \
120   2023-01-06 05:00:00   16807.81   16808.71   16778.34   16792.75    4   
121   2023-01-06 06:00:00   16792.86   16800.05   16768.88   16772.07    4   
122   2023-01-06 07:00:00   16772.09   16790.92   16767.48   16774.41    4   
123   2023-01-06 08:00:00   16774.19   16800.49   16766.93   16783.32    4   
124   2023-01-06 09:00:00   16782.74   16785.60   16742.54   16774.34    4   
...                   ...        ...        ...        ...        ...  ...   
17992 2025-01-19 23:00:00  103284.38  103284.38   99474.07  101188.60    6   
17993 2025-01-20 00:00:00  101188.15  101519.62   99396.96   99659.70    0   
17994 2025-01-20 01:00:00   99659.70  100832.64   99469.72  100536.88    0   
17995 2025-01-20 02:00:00  100536.88  102159.41  100429.72  101771.37    0   
17996 2025-01-20 03:00:00  101780.77  102069.32  101299.36  101586.55    0   

       time_hms  hour    high_20    low_20    range  
120    05

### create trade logic
Check if there are any open trades. If not, look for entry signals.
- If the entry signal is 'buy' and there are no open trades, open a buy trade for 'DE40' with a quantity of 1.
- If the entry signal is 'sell' and there are no open trades, open a sell trade for 'DE40' with a quantity of 1.
- If there are open trades, check the exit signal. If the trade is a buy and the exit signal is 'sell', close the trade. 
- If the trade is a sell and the exit signal is 'buy', close the trade.
In essence, this strategy enters a trade

In [11]:
# create trade logic
# symbol = 'DE40'
symbol = 'BTCUSDm'

def on_bar(data, trades, orders):
    
    open_trades = trades[trades['state'] == 'open']
    num_open_trades = open_trades.shape[0]
    
    # entry signal
    if data['signal'] == 'buy' and not num_open_trades:
        orders.open_trade(symbol, 1, 'buy', info={'msg': 'test'})
    
    elif data['signal'] == 'sell' and not num_open_trades:
        orders.open_trade(symbol, 1, 'sell', info={'msg2': 'test2'})
        
    # exit signal
    if num_open_trades:
        trade = open_trades.iloc[0]

        if trade['order_type'] == 'buy' and data['exit_signal'] == 'sell':
            orders.close_trade(trade)
        elif trade['order_type'] == 'sell' and data['exit_signal'] == 'buy':
            orders.close_trade(trade)


In [12]:
# backtest parameters
starting_balance = 10000
currency = 'BTCUSDm'
exchange_rate = 1
commission = -1

# backtest
bt = Backtester()
bt.set_starting_balance(starting_balance, currency=currency)
bt.set_exchange_rate(exchange_rate)
bt.set_commission(commission)

bt.set_historical_data(ohlc)
bt.set_on_bar(on_bar)

bt.run_backtest()

bt.trades

state   symbol order_type volume            open_time open_price  \
0   closed  BTCUSDm        buy      1  2023-01-08 23:00:00   16948.32   
1   closed  BTCUSDm       sell      1  2023-02-09 19:00:00   22520.15   
2   closed  BTCUSDm        buy      1  2023-02-15 12:00:00   22440.89   
3   closed  BTCUSDm       sell      1  2023-02-24 15:00:00   23791.13   
4   closed  BTCUSDm        buy      1  2023-03-13 14:00:00   22541.55   
..     ...      ...        ...    ...                  ...        ...   
57  closed  BTCUSDm        buy      1  2024-12-05 02:00:00   98290.72   
58  closed  BTCUSDm       sell      1  2024-12-19 01:00:00  100711.14   
59  closed  BTCUSDm        buy      1  2025-01-02 14:00:00   96404.47   
60  closed  BTCUSDm       sell      1  2025-01-08 11:00:00   95920.27   
61  closed  BTCUSDm        buy      1  2025-01-15 13:00:00   96930.24   

             close_time close_price sl tp               info   profit  \
0   2023-02-09 03:00:00    22816.12  0  0    {'msg': 'test'}  5867.80   
1   2023-02-15 11:00:00    22224.21  0  0  {'msg2': 'test2'}   295.94   
2   2023-02-22 15:00:00    23927.13  0  0    {'msg': 'test'}  1486.24   
3   2023-03-13 00:00:00    22103.32  0  0  {'msg2': 'test2'}  1687.81   
4   2023-04-17 11:00:00    29899.21  0  0    {'msg': 'test'}  7357.66   
..                  ...         ... .. ..                ...      ...   
57  2024-12-18 23:00:00   101037.16  0  0    {'msg': 'test'}  2746.44   
58  2025-01-02 09:00:00    96081.28  0  0  {'msg2': 'test2'}  4629.86   
59  2025-01-08 06:00:00    96522.85  0  0    {'msg': 'test'}   118.38   
60  2025-01-14 09:00:00    95490.02  0  0  {'msg2': 'test2'}   430.25   
61  2025-01-20 03:00:00   101586.55  0  0    {'msg': 'test'}  4656.31   

   commission profit_net profit_cumulative   balance  
0          -1     5866.8            5866.8   15866.8  
1          -1     294.94           6161.74  16161.74  
2          -1    1485.24           7646.98  17646.98  
3          -1    1686.81           9333.79  19333.79  
4          -1    7356.66          16690.45  26690.45  
..        ...        ...               ...       ...  
57         -1    2745.44          70286.26  80286.26  
58         -1    4628.86          74915.12  84915.12  
59         -1     117.38           75032.5   85032.5  
60         -1     429.25          75461.75  85461.75  
61         -1    4655.31          80117.06  90117.06  

[62 rows x 16 columns]

In [15]:
pnl_chart = bt.plot_pnl()
pnl_chart

In [16]:
balance_chart = bt.plot_balance()
balance_chart

In [17]:
backtest_fig = bt.visualize_backtest(indicators=['high_20', 'low_20'])
backtest_fig

In [18]:
evaluate_backtest(bt.trades)

biggest_profit 24406.9
biggest_loss -3807.73


state   symbol order_type volume           open_time open_price  \
0   closed  BTCUSDm        buy      1 2023-01-08 23:00:00   16948.32   
1   closed  BTCUSDm       sell      1 2023-02-09 19:00:00   22520.15   
2   closed  BTCUSDm        buy      1 2023-02-15 12:00:00   22440.89   
3   closed  BTCUSDm       sell      1 2023-02-24 15:00:00   23791.13   
4   closed  BTCUSDm        buy      1 2023-03-13 14:00:00   22541.55   
5   closed  BTCUSDm       sell      1 2023-04-19 23:00:00   29075.09   
7   closed  BTCUSDm       sell      1 2023-05-08 08:00:00   28002.12   
10  closed  BTCUSDm        buy      1 2023-06-20 16:00:00   27076.59   
11  closed  BTCUSDm       sell      1 2023-07-24 09:00:00    29733.0   
13  closed  BTCUSDm       sell      1 2023-08-17 00:00:00   28686.09   
16  closed  BTCUSDm        buy      1 2023-09-14 13:00:00    26462.9   
17  closed  BTCUSDm       sell      1 2023-09-24 23:00:00   26500.89   
18  closed  BTCUSDm        buy      1 2023-09-28 15:00:00   26791.52   
20  closed  BTCUSDm        buy      1 2023-10-16 13:00:00   27876.46   
22  closed  BTCUSDm        buy      1 2023-12-01 09:00:00   38296.82   
26  closed  BTCUSDm       sell      1 2024-01-18 19:00:00   41443.49   
27  closed  BTCUSDm        buy      1 2024-01-26 18:00:00    41892.7   
32  closed  BTCUSDm       sell      1 2024-04-13 19:00:00   67108.57   
36  closed  BTCUSDm        buy      1 2024-05-15 15:00:00   64511.53   
37  closed  BTCUSDm       sell      1 2024-06-11 09:00:00   67439.26   
40  closed  BTCUSDm        buy      1 2024-07-13 22:00:00   58718.15   
43  closed  BTCUSDm       sell      1 2024-07-31 20:00:00   65253.83   
48  closed  BTCUSDm        buy      1 2024-09-13 21:00:00   59871.67   
51  closed  BTCUSDm        buy      1 2024-10-14 07:00:00   64086.42   
55  closed  BTCUSDm        buy      1 2024-11-06 03:00:00   73130.27   
57  closed  BTCUSDm        buy      1 2024-12-05 02:00:00   98290.72   
58  closed  BTCUSDm       sell      1 2024-12-19 01:00:00  100711.14   
59  closed  BTCUSDm        buy      1 2025-01-02 14:00:00   96404.47   
60  closed  BTCUSDm       sell      1 2025-01-08 11:00:00   95920.27   
61  closed  BTCUSDm        buy      1 2025-01-15 13:00:00   96930.24   

            close_time close_price sl tp               info    profit  \
0  2023-02-09 03:00:00    22816.12  0  0    {'msg': 'test'}   5867.80   
1  2023-02-15 11:00:00    22224.21  0  0  {'msg2': 'test2'}    295.94   
2  2023-02-22 15:00:00    23927.13  0  0    {'msg': 'test'}   1486.24   
3  2023-03-13 00:00:00    22103.32  0  0  {'msg2': 'test2'}   1687.81   
4  2023-04-17 11:00:00    29899.21  0  0    {'msg': 'test'}   7357.66   
5  2023-04-26 08:00:00    28375.74  0  0  {'msg2': 'test2'}    699.35   
7  2023-05-28 17:00:00    27255.43  0  0  {'msg2': 'test2'}    746.69   
10 2023-07-17 18:00:00    30024.56  0  0    {'msg': 'test'}   2947.97   
11 2023-08-01 23:00:00     29228.6  0  0  {'msg2': 'test2'}    504.40   
13 2023-08-23 16:00:00    26143.15  0  0  {'msg2': 'test2'}   2542.94   
16 2023-09-21 13:00:00     26636.5  0  0    {'msg': 'test'}    173.60   
17 2023-09-27 11:00:00    26426.33  0  0  {'msg2': 'test2'}     74.56   
18 2023-10-11 02:00:00    27433.34  0  0    {'msg': 'test'}    641.82   
20 2023-11-14 18:00:00    36063.08  0  0    {'msg': 'test'}   8186.62   
22 2023-12-11 02:00:00    43167.19  0  0    {'msg': 'test'}   4870.37   
26 2024-01-26 16:00:00    41371.33  0  0  {'msg2': 'test2'}     72.16   
27 2024-03-16 23:00:00     66299.6  0  0    {'msg': 'test'}  24406.90   
32 2024-04-22 03:00:00    64808.99  0  0  {'msg2': 'test2'}   2299.58   
36 2024-06-11 02:00:00    68688.28  0  0    {'msg': 'test'}   4176.75   
37 2024-06-30 22:00:00    61873.38  0  0  {'msg2': 'test2'}   5565.88   
40 2024-07-25 01:00:00    65491.83  0  0    {'msg': 'test'}   6773.68   
43 2024-08-08 21:00:00    59549.67  0  0  {'msg2': 'test2'}   5704.16   
48 2024-10-01 20:00:00    61736.28  0  0    {'msg': 'test'}   1864.61   
51 2024-10-23 08:00:

state   symbol order_type volume           open_time open_price  \
6   closed  BTCUSDm        buy      1 2023-04-26 09:00:00   28738.21   
8   closed  BTCUSDm        buy      1 2023-05-28 18:00:00   27360.06   
9   closed  BTCUSDm       sell      1 2023-06-05 16:00:00   25972.64   
12  closed  BTCUSDm        buy      1 2023-08-02 00:00:00   29682.27   
14  closed  BTCUSDm        buy      1 2023-08-23 17:00:00   26393.31   
15  closed  BTCUSDm        buy      1 2023-09-07 21:00:00   25998.21   
19  closed  BTCUSDm       sell      1 2023-10-11 03:00:00   27116.67   
21  closed  BTCUSDm       sell      1 2023-11-21 23:00:00   36388.76   
23  closed  BTCUSDm        buy      1 2023-12-20 13:00:00   42955.83   
24  closed  BTCUSDm       sell      1 2023-12-26 17:00:00   42270.08   
25  closed  BTCUSDm        buy      1 2024-01-02 00:00:00   44238.93   
28  closed  BTCUSDm       sell      1 2024-03-19 08:00:00   64604.93   
29  closed  BTCUSDm        buy      1 2024-03-25 15:00:00   69403.34   
30  closed  BTCUSDm       sell      1 2024-04-02 02:00:00   69390.44   
31  closed  BTCUSDm        buy      1 2024-04-08 07:00:00   69754.28   
33  closed  BTCUSDm        buy      1 2024-04-22 05:00:00   65732.87   
34  closed  BTCUSDm       sell      1 2024-04-29 03:00:00   62701.45   
35  closed  BTCUSDm       sell      1 2024-05-08 20:00:00   62171.37   
38  closed  BTCUSDm        buy      1 2024-07-01 01:00:00   62889.51   
39  closed  BTCUSDm       sell      1 2024-07-04 08:00:00   58140.22   
41  closed  BTCUSDm       sell      1 2024-07-25 02:00:00   64487.27   
42  closed  BTCUSDm        buy      1 2024-07-27 13:00:00   68444.06   
44  closed  BTCUSDm        buy      1 2024-08-08 22:00:00   61212.46   
45  closed  BTCUSDm       sell      1 2024-08-15 20:00:00   57032.08   
46  closed  BTCUSDm        buy      1 2024-08-20 05:00:00   60900.51   
47  closed  BTCUSDm       sell      1 2024-09-04 01:00:00   57166.87   
49  closed  BTCUSDm        buy      1 2024-10-07 00:00:00   62824.89   
50  closed  BTCUSDm       sell      1 2024-10-09 19:00:00   61127.73   
52  closed  BTCUSDm       sell      1 2024-10-23 16:00:00   66109.39   
53  closed  BTCUSDm        buy      1 2024-10-28 19:00:00   69166.04   
54  closed  BTCUSDm       sell      1 2024-11-03 14:00:00   68019.72   
56  closed  BTCUSDm       sell      1 2024-11-26 10:00:00   93566.06   

            close_time close_price sl tp               info   profit  \
6  2023-05-08 07:00:00    28197.91  0  0    {'msg': 'test'}  -540.30   
8  2023-06-05 15:00:00    26807.37  0  0    {'msg': 'test'}  -552.69   
9  2023-06-17 05:00:00    26354.15  0  0  {'msg2': 'test2'}  -381.51   
12 2023-08-16 23:00:00    28872.66  0  0    {'msg': 'test'}  -809.61   
14 2023-09-01 17:00:00    25766.51  0  0    {'msg': 'test'}  -626.80   
15 2023-09-11 14:00:00    25592.66  0  0    {'msg': 'test'}  -405.55   
19 2023-10-16 05:00:00     27233.0  0  0  {'msg2': 'test2'}  -116.33   
21 2023-11-24 15:00:00    37780.42  0  0  {'msg2': 'test2'} -1391.66   
23 2023-12-26 09:00:00     42682.4  0  0    {'msg': 'test'}  -273.43   
24 2024-01-01 23:00:00    43513.47  0  0  {'msg2': 'test2'} -1243.39   
25 2024-01-12 22:00:00    43416.41  0  0    {'msg': 'test'}  -822.52   
28 2024-03-25 14:00:00    67987.76  0  0  {'msg2': 'test2'} -3382.83   
29 2024-04-01 15:00:00    68889.98  0  0    {'msg': 'test'}  -513.36   
30 2024-04-07 16:00:00    69544.17  0  0  {'msg2': 'test2'}  -153.73   
31 2024-04-12 18:00:00    68099.73  0  0    {'msg': 'test'} -1654.55   
33 2024-04-27 01:00:00    63151.47  0  0    {'msg': 'test'} -2581.40   
34 2024-05-06 08:00:00    64519.72  0  0  {'msg2': 'test2'} -1818.27   
35 2024-05-15 12:00:00     62450.6  0  0  {'msg2': 'test2'}  -279.23   
38 2024-07-04 01:00:00    60377.24  0  0    {'msg': 'test'} -2512.27   
39 2024-07-10 04:00:00    58220.25  0  0  {'msg2': 'test2'}   -80.03   
41 2024-07-27 12:00:00    68237.83  0  0  {'msg2': 'test2'} -3750.56   
42 2024-07-31 19:00:00    66498.35  0  0    

avg_win 4201.698
avg_loss -1433.4962500000001
count_profit_trades 30
count_loss_trades 32
win_rate 0.94
rrr 2.93


order_type    profit
0        buy  82350.60
1       sell  -2171.54

state   symbol order_type volume           open_time open_price  \
0   closed  BTCUSDm        buy      1 2023-01-08 23:00:00   16948.32   
1   closed  BTCUSDm       sell      1 2023-02-09 19:00:00   22520.15   
2   closed  BTCUSDm        buy      1 2023-02-15 12:00:00   22440.89   
3   closed  BTCUSDm       sell      1 2023-02-24 15:00:00   23791.13   
4   closed  BTCUSDm        buy      1 2023-03-13 14:00:00   22541.55   
..     ...      ...        ...    ...                 ...        ...   
57  closed  BTCUSDm        buy      1 2024-12-05 02:00:00   98290.72   
58  closed  BTCUSDm       sell      1 2024-12-19 01:00:00  100711.14   
59  closed  BTCUSDm        buy      1 2025-01-02 14:00:00   96404.47   
60  closed  BTCUSDm       sell      1 2025-01-08 11:00:00   95920.27   
61  closed  BTCUSDm        buy      1 2025-01-15 13:00:00   96930.24   

            close_time close_price sl tp               info   profit  \
0  2023-02-09 03:00:00    22816.12  0  0    {'msg': 'test'}  5867.80   
1  2023-02-15 11:00:00    22224.21  0  0  {'msg2': 'test2'}   295.94   
2  2023-02-22 15:00:00    23927.13  0  0    {'msg': 'test'}  1486.24   
3  2023-03-13 00:00:00    22103.32  0  0  {'msg2': 'test2'}  1687.81   
4  2023-04-17 11:00:00    29899.21  0  0    {'msg': 'test'}  7357.66   
..                 ...         ... .. ..                ...      ...   
57 2024-12-18 23:00:00   101037.16  0  0    {'msg': 'test'}  2746.44   
58 2025-01-02 09:00:00    96081.28  0  0  {'msg2': 'test2'}  4629.86   
59 2025-01-08 06:00:00    96522.85  0  0    {'msg': 'test'}   118.38   
60 2025-01-14 09:00:00    95490.02  0  0  {'msg2': 'test2'}   430.25   
61 2025-01-20 03:00:00   101586.55  0  0    {'msg': 'test'}  4656.31   

   commission profit_net profit_cumulative   balance  dayofweek  
0          -1     5866.8            5866.8   15866.8          3  
1          -1     294.94           6161.74  16161.74          2  
2          -1    1485.24           7646.98  17646.98          2  
3          -1    1686.81           9333.79  19333.79          0  
4          -1    7356.66          16690.45  26690.45          0  
..        ...        ...               ...       ...        ...  
57         -1    2745.44          70286.26  80286.26          2  
58         -1    4628.86          74915.12  84915.12          3  
59         -1     117.38           75032.5   85032.5          2  
60         -1     429.25          75461.75  85461.75          1  
61         -1    4655.31          80117.06  90117.06          0  

[62 rows x 17 columns]

state   symbol order_type volume           open_time open_price  \
0   closed  BTCUSDm        buy      1 2023-01-08 23:00:00   16948.32   
1   closed  BTCUSDm       sell      1 2023-02-09 19:00:00   22520.15   
2   closed  BTCUSDm        buy      1 2023-02-15 12:00:00   22440.89   
3   closed  BTCUSDm       sell      1 2023-02-24 15:00:00   23791.13   
4   closed  BTCUSDm        buy      1 2023-03-13 14:00:00   22541.55   
..     ...      ...        ...    ...                 ...        ...   
57  closed  BTCUSDm        buy      1 2024-12-05 02:00:00   98290.72   
58  closed  BTCUSDm       sell      1 2024-12-19 01:00:00  100711.14   
59  closed  BTCUSDm        buy      1 2025-01-02 14:00:00   96404.47   
60  closed  BTCUSDm       sell      1 2025-01-08 11:00:00   95920.27   
61  closed  BTCUSDm        buy      1 2025-01-15 13:00:00   96930.24   

            close_time close_price sl tp               info   profit  \
0  2023-02-09 03:00:00    22816.12  0  0    {'msg': 'test'}  5867.80   
1  2023-02-15 11:00:00    22224.21  0  0  {'msg2': 'test2'}   295.94   
2  2023-02-22 15:00:00    23927.13  0  0    {'msg': 'test'}  1486.24   
3  2023-03-13 00:00:00    22103.32  0  0  {'msg2': 'test2'}  1687.81   
4  2023-04-17 11:00:00    29899.21  0  0    {'msg': 'test'}  7357.66   
..                 ...         ... .. ..                ...      ...   
57 2024-12-18 23:00:00   101037.16  0  0    {'msg': 'test'}  2746.44   
58 2025-01-02 09:00:00    96081.28  0  0  {'msg2': 'test2'}  4629.86   
59 2025-01-08 06:00:00    96522.85  0  0    {'msg': 'test'}   118.38   
60 2025-01-14 09:00:00    95490.02  0  0  {'msg2': 'test2'}   430.25   
61 2025-01-20 03:00:00   101586.55  0  0    {'msg': 'test'}  4656.31   

   commission profit_net profit_cumulative   balance  dayofweek  current_max  \
0          -1     5866.8            5866.8   15866.8          3      5866.80   
1          -1     294.94           6161.74  16161.74          2      6161.74   
2          -1    1485.24           7646.98  17646.98          2      7646.98   
3          -1    1686.81           9333.79  19333.79          0      9333.79   
4          -1    7356.66          16690.45  26690.45          0     16690.45   
..        ...        ...               ...       ...        ...          ...   
57         -1    2745.44          70286.26  80286.26          2     71349.55   
58         -1    4628.86          74915.12  84915.12          3     74915.12   
59         -1     117.38           75032.5   85032.5          2     75032.50   
60         -1     429.25          75461.75  85461.75          1     75461.75   
61         -1    4655.31          80117.06  90117.06          0     80117.06   

   drawdown  
0       0.0  
1       0.0  
2       0.0  
3       0.0  
4       0.0  
..      ...  
57 -1063.29  
58      0.0  
59      0.0  
60      0.0  
61      0.0  

[62 rows x 19 columns]

ValueError: Plotly Express cannot process wide-form data with columns of different type.